In [1]:
!apt install swig cmake ffmpeg xvfb python3-opengl
!pip install stable-baselines3==2.0.0a5 gymnasium[box2d] huggingface_sb3 pyvirtualdisplay imageio[ffmpeg]

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
cmake is already the newest version (3.22.1-1ubuntu1.22.04.2).
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
The following additional packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 swig4.0 x11-xkb-utils xfonts-base
  xfonts-encodings xfonts-utils xserver-common
Suggested packages:
  libgle3 python3-numpy swig-doc swig-examples swig4.0-examples swig4.0-doc
The following NEW packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 python3-opengl swig swig4.0
  x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils xserver-common xvfb
0 upgraded, 14 newly installed, 0 to remove and 45 not upgraded.
Need to get 9,755 kB of archives.
After this operation, 25.6 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 freeglut3 amd64 2.8.1-6 [74.0 kB]
Get:2 http://

In [ ]:
import os
os.kill(os.getpid(), 9)

In [1]:
from pyvirtualdisplay import Display
virtual_display = Display(visible=0, size=(1400, 900))
virtual_display.start()

In [2]:
import gymnasium as gym
env = gym.make("BipedalWalker-v3", hardcore=True)
env.reset()

(array([ 2.7473615e-03, -1.7453976e-05,  1.3577418e-03, -1.5999883e-02,
         9.1910392e-02, -1.7917611e-03,  8.6029738e-01,  2.7268257e-03,
         1.0000000e+00,  3.2314595e-02, -1.7916345e-03,  8.5384989e-01,
         1.2671478e-03,  1.0000000e+00,  4.4081411e-01,  4.4582021e-01,
         4.6142289e-01,  4.8955029e-01,  5.3410292e-01,  6.0246116e-01,
         7.0914906e-01,  8.8593203e-01,  1.0000000e+00,  1.0000000e+00],
       dtype=float32),
 {})

In [3]:
print("_____OBSERVATION SPACE_____ \n")
print("Observation Space Shape", env.observation_space.shape)
print("Sample observation", env.observation_space.sample())

_____OBSERVATION SPACE_____ 

Observation Space Shape (24,)
Sample observation [ 2.2148275  -2.4581616   1.4768916  -2.4018087  -0.37689734  2.4662356
  2.9171126   0.557763    0.45240203  3.0006154  -1.0644464   0.71462756
 -1.9203025   0.03077204  0.53521484  0.96251464 -0.2056138  -0.682782
 -0.8920208   0.66592366  0.27296963 -0.8674961  -0.5933538   0.09664863]


In [4]:
print("\n _____ACTION SPACE_____ \n")
print("Action Space Shape", env.action_space.shape)
print("Action Space Sample", env.action_space.sample())


 _____ACTION SPACE_____ 

Action Space Shape (4,)
Action Space Sample [0.6653655  0.20582972 0.1703576  0.20674136]


In [5]:
from stable_baselines3.common.env_util import make_vec_env
env = make_vec_env('BipedalWalker-v3', n_envs=16)

In [6]:
from stable_baselines3 import SAC
model = SAC(
    policy = 'MlpPolicy',
    env = env,
    verbose=1)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Using cuda device


In [7]:
from wasabi import Printer
import numpy as np
from stable_baselines3.common.base_class import BaseAlgorithm
from pathlib import Path
import tempfile
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import (
    DummyVecEnv,
    VecEnv,
    VecVideoRecorder,
)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [8]:
msg = Printer()

In [9]:
def generate_replay(
    model: BaseAlgorithm,
    eval_env: VecEnv,
    video_length: int,
    is_deterministic: bool,
    local_path: Path,
):
    """
    Generate a replay video of the agent
    :param model: trained model
    :param eval_env: environment used to evaluate the agent
    :param video_length: length of the video (in timesteps)
    :param is_deterministic: use deterministic or stochastic actions
    :param local_path: path of the local repository
    """
    # This is another temporary directory for video outputs
    # SB3 created a -step-0-to-... meta files as well as other
    # artifacts which we don't want in the repo.
    with tempfile.TemporaryDirectory() as tmpdirname:
        # Step 1: Create the VecVideoRecorder
        env = VecVideoRecorder(
            eval_env,
            tmpdirname,
            record_video_trigger=lambda x: x == 0,
            video_length=video_length,
            name_prefix="",
        )

        obs = env.reset()
        lstm_states = None
        episode_starts = np.ones((env.num_envs,), dtype=bool)

        try:
            for _ in range(video_length):
                action, lstm_states = model.predict(
                    obs,
                    state=lstm_states,
                    episode_start=episode_starts,
                    deterministic=is_deterministic,
                )
                obs, _, episode_starts, _ = env.step(action)

            # Save the video
            env.close()

            # Convert the video with x264 codec
            inp = env.video_recorder.path
            out = local_path
            os.system(f"ffmpeg -y -i {inp} -vcodec h264 {out}".format(inp, out))
            print(f"Video saved to: {out}")
        except KeyboardInterrupt:
            pass
        except Exception as e:
            msg.fail(str(e))
            # Add a message for video
            msg.fail(
                "We are unable to generate a replay of your agent"
            )

In [10]:
import os
#create a directory to save the videos
video_dir = "/content/videos"
if not os.path.exists(video_dir):
    os.makedirs(video_dir)

In [11]:
env_id = "BipedalWalker-v3"
# Train and generate video at every 100000 steps, adjust the timesteps to your liking
for i in range(0, 200000, 10000):
    model.learn(total_timesteps=10000)
    # Save the model
    model_name = "sac-BipedalWalker-v3"
    model.save(model_name)
    video_name = f"replay_{i + 10000}.mp4"
    generate_replay(
        model=model,
        eval_env=DummyVecEnv([lambda: Monitor(gym.make(env_id, hardcore=True, render_mode="rgb_array"))]),
        video_length=1000,
        is_deterministic=True,
        local_path=os.path.join(video_dir, video_name)
    )

model_name = "sac-BipedalWalker-v3"
model.save(model_name)


---------------------------------
| rollout/           |          |
|    ep_len_mean     | 66.5     |
|    ep_rew_mean     | -105     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 494      |
|    time_elapsed    | 2        |
|    total_timesteps | 1440     |
| train/             |          |
|    actor_loss      | -5.52    |
|    critic_loss     | 81.5     |
|    ent_coef        | 0.976    |
|    ent_coef_loss   | -0.166   |
|    learning_rate   | 0.0003   |
|    n_updates       | 83       |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 87.2     |
|    ep_rew_mean     | -105     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 548      |
|    time_elapsed    | 3        |
|    total_timesteps | 1936     |
| train/             |          |
|    actor_loss      | -5.36    |
|    critic_loss     | 0.389    |
|    ent_coef 

Moviepy - Done !
Moviepy - video ready /tmp/tmpe99fqdw4/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_10000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 52       |
|    ep_rew_mean     | -111     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 1055     |
|    time_elapsed    | 0        |
|    total_timesteps | 896      |
| train/             |          |
|    actor_loss      | -8.98    |
|    critic_loss     | 0.418    |
|    ent_coef        | 0.819    |
|    ent_coef_loss   | -1.34    |
|    learning_rate   | 0.0003   |
|    n_updates       | 668      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 64.8     |
|    ep_rew_mean     | -109     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 1043     |
|    time_elapsed    | 1        |
|    total_timesteps

Moviepy - Done !
Moviepy - video ready /tmp/tmpg1cxof_c/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_20000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 55.2     |
|    ep_rew_mean     | -110     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 989      |
|    time_elapsed    | 0        |
|    total_timesteps | 976      |
| train/             |          |
|    actor_loss      | -12.7    |
|    critic_loss     | 30.5     |
|    ent_coef        | 0.68     |
|    ent_coef_loss   | -2.54    |
|    learning_rate   | 0.0003   |
|    n_updates       | 1292     |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 64.1     |
|    ep_rew_mean     | -110     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 979      |
|    time_elapsed    | 1        |
|    total_timesteps

Moviepy - Done !
Moviepy - video ready /tmp/tmp65pbl4ww/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_30000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 68.2     |
|    ep_rew_mean     | -100     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 785      |
|    time_elapsed    | 1        |
|    total_timesteps | 1216     |
| train/             |          |
|    actor_loss      | -15.7    |
|    critic_loss     | 18.2     |
|    ent_coef        | 0.563    |
|    ent_coef_loss   | -3.78    |
|    learning_rate   | 0.0003   |
|    n_updates       | 1926     |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 75.2     |
|    ep_rew_mean     | -102     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 760      |
|    time_elapsed    | 1        |
|    total_timesteps

Moviepy - Done !
Moviepy - video ready /tmp/tmpeeju_7uw/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_40000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 59.8     |
|    ep_rew_mean     | -108     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 1047     |
|    time_elapsed    | 1        |
|    total_timesteps | 1248     |
| train/             |          |
|    actor_loss      | -17.8    |
|    critic_loss     | 9.31     |
|    ent_coef        | 0.468    |
|    ent_coef_loss   | -5.03    |
|    learning_rate   | 0.0003   |
|    n_updates       | 2547     |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 72.6     |
|    ep_rew_mean     | -104     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 1056     |
|    time_elapsed    | 2        |
|    total_timesteps

...

Moviepy - Done !
Moviepy - video ready /tmp/tmp8cf25k5n/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_160000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 90.5     |
|    ep_rew_mean     | -124     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 871      |
|    time_elapsed    | 3        |
|    total_timesteps | 3120     |
| train/             |          |
|    actor_loss      | -18.4    |
|    critic_loss     | 1.03     |
|    ent_coef        | 0.054    |
|    ent_coef_loss   | -11.7    |
|    learning_rate   | 0.0003   |
|    n_updates       | 10092    |
---------------------------------
Saving video to /tmp/tmpmxq_im2v/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmpmxq_im2v/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmpmxq_im2v/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmpmxq_im2v/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_170000.mp4
Saving video to /tmp/tmp07q7viuw/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmp07q7viuw/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmp07q7viuw/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmp07q7viuw/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_180000.mp4
Saving video to /tmp/tmpcjmvkse8/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmpcjmvkse8/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmpcjmvkse8/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmpcjmvkse8/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_190000.mp4
Saving video to /tmp/tmp43ctx1ik/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmp43ctx1ik/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmp43ctx1ik/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmp43ctx1ik/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_200000.mp4


In [12]:
with open(os.path.join(video_dir, "filelist.txt"), "w") as f:
    for i in range(0, 200000, 10000):
        video_name = f"replay_{i + 10000}.mp4"
        f.write(f"file '{os.path.join(video_dir, video_name)}'\n")
# Concatenate all the videos into one
os.system(f"ffmpeg -f concat -safe 0 -i {os.path.join(video_dir, 'filelist.txt')} -c copy {os.path.join(video_dir, 'replay_all.mp4')}")

0

In [13]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('videos/replay_all.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [14]:
from stable_baselines3.common.evaluation import evaluate_policy
eval_env = Monitor(gym.make("BipedalWalker-v3"))
mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10, deterministic=True)
print(f"mean_reward={mean_reward:.2f} +/- {std_reward}")

mean_reward=-50.32 +/- 7.490672961711549
